**Author**: Anand Gajaria, Data Scientist, [LinkedIn](https://www.linkedin.com/in/anand-gajaria-7b2272181/)

## Importing Required Libraries

We begin by importing essential Python libraries. In particular:

- **osmnx**: A Python package to download, model, analyze, and visualize street networks and other geospatial data from OpenStreetMap.
- **matplotlib.pyplot**: A plotting library for creating static, animated, and interactive visualizations in Python.
- **folium**: A Python library for visualizing geospatial data on interactive Leaflet mapty.
- **folium.GeoJsonTooltip**: A tool for displaying custom tooltips when hovering over GeoJSON features on a Folium ions.
- **pandas**: A powerful data analysis and manipulation library for Python, offering data structures like DataFrames.
- **shapely.ops.nearest_points**: A Shapely function to find the nearest points between two geometric objects.
- **shapely.ops.transform**: A Shapely function to apply coordinate transformations to geometries.
- **pyproj**: A Python interface to PROJ, used for cartographic projections and coordinate transformations.


These libraries help us download, clean, process, and visualize geospatial vector data for urban planning.


In [13]:
import osmnx as ox
import matplotlib.pyplot as plt
import folium
from folium.plugins import MarkerCluster
from folium import GeoJsonTooltip
import branca.colormap as cm
import pandas as pd
from shapely.ops import nearest_points
from shapely.ops import transform
import pyproj
import geopandas as gpd

## Defining the Study Area

We define the geographic location (city or region) of interest. In this project, our focus is on **Berlin**, and we use OSM data to extract features like:

- Schools
- Hosp
works

This forms the basis for our spatial analysis and visualization.


In [30]:
# Define the city
place_name = "Berlin, Germany"

# 2. Download amenities: schools
schools_gdf = ox.geometries_from_place(place_name, tags={"amenity": "school"})

# 3. Download amenities: hospitals
hospitals_gdf = ox.geometries_from_place(place_name, tags={"amenity": "hospital"})

# 4. Download administrative boundary
admin_gdf = ox.geocode_to_gdf(place_name)

C:\Users\dmz-admin\AppData\Local\Temp\ipykernel_17328\691144935.py:5: FutureWarning: The `geometries` module and `geometries_from_X` functions have been renamed the `features` module and `features_from_X` functions. Use these instead. The `geometries` module and function names are deprecated and will be removed in the v2.0.0 release.
  schools_gdf = ox.geometries_from_place(place_name, tags={"amenity": "school"})
C:\Users\dmz-admin\anaconda3\envs\gis_analysis\Lib\site-packages\osmnx\features.py:292: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  polygon = gdf_place["geometry"].unary_union
C:\Users\dmz-admin\AppData\Local\Temp\ipykernel_17328\691144935.py:8: FutureWarning: The `geometries` module and `geometries_from_X` functions have been renamed the `features` module and `features_from_X` functions. Use these instead. The `geometries` module and function names are deprecated and will be removed in the v2.0.0 release.
  hospitals_

In [33]:
schools_gdf.head()

access barrier                   geometry addr:city  \
element_type osmid                                                           
node         237838613    NaN     NaN  POINT (13.33846 52.47997)    Berlin   
             256912446    NaN     NaN  POINT (13.28804 52.53944)    Berlin   
             256913234    NaN     NaN  POINT (13.24163 52.52114)    Berlin   
             256913872    NaN     NaN  POINT (13.28833 52.53766)    Berlin   
             268915405    NaN     NaN  POINT (13.38146 52.45454)       NaN   

                       addr:country addr:housenumber addr:postcode  \
element_type osmid                                                   
node         237838613           DE                8         10825   
             256912446           DE            34-42         13627   
             256913234           DE                1         14053   
             256913872           DE               22         13627   
             268915405          NaN            13-18         12105   

                                     addr:street          addr:suburb amenity  \
element_type osmid                                                              
node         237838613               Mettestraße           Schöneberg  school   
             256912446                  Halemweg  Charlottenburg-Nord  school   
             256913234  Prinz-Friedrich-Karl-Weg              Westend  school   
             256913872                  Halemweg              Westend  school   
             268915405            Viktoriastraße            Tempelhof  school   

                        ... architect building:levels:underground smoking  \
element_type osmid      ...                                                 
node         237838613  ...       NaN                         NaN     NaN   
             256912446  ...       NaN                         NaN     NaN   
             256913234  ...       NaN                         NaN     NaN   
             256913872  ...       NaN                         NaN     NaN   
             268915405  ...       NaN                         NaN     NaN   

                       temporary old_name:1860 old_name:1942 old_name:1960  \
element_type osmid                                                           
node         237838613       NaN           NaN           NaN           NaN   
             256912446       NaN           NaN           NaN           NaN   
             256913234       NaN           NaN           NaN           NaN   
             256913872       NaN           NaN           NaN           NaN   
             268915405       NaN           NaN           NaN           NaN   

                       old_name:1993-2012 old_name:2 ways  
element_type osmid                                         
node         237838613                NaN        NaN  NaN  
             256912446                NaN        NaN  NaN  
             256913234                NaN        NaN  NaN  
             256913872                NaN        NaN  NaN  
             268915405                NaN        NaN  NaN  

[5 rows x 155 columns]

In [35]:
schools_polygons_cleaned.head()

element_type    osmid                                           geometry  \
0          way  4675785  POLYGON ((13.34643 52.53434, 13.34645 52.53429...   
1          way  4675905  POLYGON ((13.35734 52.52275, 13.35732 52.5227,...   
2          way  4675932  POLYGON ((13.35918 52.52378, 13.35915 52.52368...   
3          way  4677755  POLYGON ((13.3405 52.5327, 13.3405 52.53295, 1...   
4          way  4703540  POLYGON ((13.33522 52.53184, 13.33583 52.53179...   

                                             name amenity addr:city  \
0                              Hedwig-Dohm-Schule  school    Berlin   
1                            Moabiter Grundschule  school    Berlin   
2     Oberstufenzentrum Banken und Versicherungen  school    Berlin   
3                      Schul-Umwelt-Zentrum Mitte  school    Berlin   
4  Theodor-Heuss-Gemeinschaftsschule (Grundstufe)  school    Berlin   

  addr:postcode addr:suburb    addr:street operator:type isced:level religion  \
0         10559      Moabit  Stephanstraße           NaN         NaN      NaN   
1         10557      Moabit     Paulstraße           NaN         NaN      NaN   
2         10557      Moabit     Alt-Moabit           NaN         NaN      NaN   
3         10551      Moabit   Birkenstraße           NaN         NaN      NaN   
4         10551         NaN  Siemensstraße        public         NaN      NaN   

  wheelchair       geom_type  
0        NaN  school_polygon  
1        NaN  school_polygon  
2        NaN  school_polygon  
3        NaN  school_polygon  
4         no  school_polygon

## Data Processing

#### Dropping Sparse Columns

This function helps us clean our dataset by removing any columns where more than 95% of values are missing.

This simplifies the data, making it easier to analyze and visualize later.


In [3]:
def drop_sparse_columns(gdf, threshold=0.95):
    """Drop columns with more than `threshold` fraction of null values."""
    null_fraction = gdf.isnull().mean()
    keep_columns = null_fraction[null_fraction < threshold].index
    return gdf[keep_columns]

# Example usage with your Berlin datasets
schools_cleaned = drop_sparse_columns(schools_gdf)
hospitals_cleaned = drop_sparse_columns(hospitals_gdf)

#### Splitting Data by Geometry Type

In this function, we separate a single GeoDataFrame into three based on geometry:

- `Point` (e.g., school locations)
- `Polygon` (e.g., school buildings or zones)

This is important because different geometry types are suited to different types of analysis.


In [4]:
def separate_geometries(gdf, name=""):
    """
    Splits a GeoDataFrame into point, line, and polygon subsets.
    Adds a 'geom_type' label to each.
    """
    points = gdf[gdf.geom_type == "Point"].copy()
    lines = gdf[gdf.geom_type == "LineString"].copy()
    polygons = gdf[gdf.geom_type.isin(["Polygon", "MultiPolygon"])].copy()
    
    points["geom_type"] = f"{name}_point"
    polygons["geom_type"] = f"{name}_polygon"
    
    return points, polygons

# Separate for schools
schools_points, schools_polygons = separate_geometries(schools_cleaned, name="school")

# Separate for hospitals
hospitals_points, hospitals_polygons = separate_geometries(hospitals_cleaned, name="hospital")



In [5]:
schools_points = schools_points.reset_index()
schools_polygons = schools_polygons.reset_index()
hospitals_points = hospitals_points.reset_index()
hospitals_polygons = hospitals_polygons.reset_index()

#### Cleaning and Filtering Data

This function selects only the most relevant columns from the school dataset.

The goal is to retain information useful for accessibility and proximity analysis, such as:

- Name
- Address
- Amenity type
- Wheelchair accessibility

In [28]:
schools_points.columns

Index(['element_type', 'osmid', 'geometry', 'addr:city', 'addr:country',
       'addr:housenumber', 'addr:postcode', 'addr:street', 'addr:suburb',
       'amenity', 'email', 'fax', 'name', 'name:etymology:wikidata',
       'operator', 'operator:type', 'operator:wikidata', 'phone', 'ref',
       'school', 'website', 'wheelchair', 'wikidata', 'wikipedia',
       'contact:fax', 'contact:phone', 'contact:website', 'contact:email',
       'grades', 'religion', 'check_date', 'isced:level', 'old_name',
       'toilets:wheelchair', 'source', 'description', 'wikimedia_commons',
       'nodes', 'building', 'geom_type'],
      dtype='object')

In [6]:
def clean_school_columns(gdf):
    keep_cols = [
        'element_type', 'osmid', 'geometry', 'name', 'amenity',
        'addr:city', 'addr:postcode', 'addr:suburb', 'addr:street',
        'operator:type', 'isced:level', 'religion',
        'wheelchair', 'geom_type'
    ]
    # Keep only if the column exists
    cols_to_keep = [col for col in keep_cols if col in gdf.columns]
    return gdf[cols_to_keep]

In [7]:
schools_points_cleaned = clean_school_columns(schools_points)
schools_polygons_cleaned = clean_school_columns(schools_polygons)

In [8]:
def clean_hospital_columns(gdf):
    keep_cols = [
        'element_type', 'osmid', 'geometry',
        'name', 'amenity', 'healthcare', 'healthcare:speciality',
        'emergency', 'operator:type',
        'addr:city', 'addr:postcode', 'addr:suburb', 'addr:street',
        'wheelchair', 'geom_type'
    ]
    cols_to_keep = [col for col in keep_cols if col in gdf.columns]
    return gdf[cols_to_keep]

In [9]:
hospitals_points_cleaned = clean_school_columns(hospitals_points)
hospitals_polygons_cleaned = clean_school_columns(hospitals_polygons)

## Visualization: Distribution of School Buildings in Berlin

This map displays the locations of school buildings (as polygon footprints) overlaid on the Berlin administrative boundary.

### Key Observations:
- **Widespread distribution** of schools across the city indicates an effort toward decentralized educational infrastructure.
- The **central and southern parts** of Berlin show particularly high concentrations of school buildings.
- Some **peripheral districts** (especially in the north and southeast) appear to have **fewer schools**, which may indicate:
  - Lower residential density
  - Less development
  - Or potential service gaps

### Why This Matters:
Understanding the **physical presence** and **spatial density** of schools is essential for Urban planning.


In [10]:
map_schools_polygons = folium.Map(location=[52.52, 13.405], zoom_start=11, tiles='CartoDB positron')

# Add hospital buildings as polygons
folium.GeoJson(
    schools_polygons_cleaned,
    name="School Buildings",
    style_function=lambda x: {"color": "darkblue", "fillOpacity": 0.3},
    tooltip=folium.GeoJsonTooltip(fields=["name"], aliases=["Hospital"])
).add_to(map_schools_polygons)

# Make sure it's in the correct CRS for folium (WGS84)
admin_boundary = admin_gdf.to_crs(epsg=4326)

# Add Berlin boundary on top of the school polygons map
folium.GeoJson(
    admin_boundary,
    name="Berlin Boundary",
    style_function=lambda feature: {
        "color": "black",
        "weight": 2,
        "fillOpacity": 0
    },
    tooltip=folium.GeoJsonTooltip(fields=["name"], aliases=["District"])
).add_to(map_schools_polygons)

# Add layer control
folium.LayerControl().add_to(map_schools_polygons)

# Display the map
map_schools_polygons

In [14]:
districts_gdf = gpd.read_file('bezirksgrenzen.geojson').drop(columns = ['gml_id', 'Land_schluessel','Schluessel_gesamt'])

In [15]:
districts_gdf = districts_gdf.rename(columns={
    "Gemeinde_name": "district",
    "Gemeinde_schluessel": "district_code",
    "Land_name": "state"
})

In [16]:
# Step 1: Spatial Join - assign each school to a district based on geometry
# This joins school polygons to the districts they fall within
schools_in_districts = gpd.sjoin(
    schools_polygons_cleaned,  # GeoDataFrame of school buildings
    districts_gdf,             # GeoDataFrame of Berlin districts
    predicate="within"         # Only keep schools located *within* district boundaries
)

# Step 2: Group and count - number of schools in each district
# This counts how many schools are assigned to each district
school_counts = schools_in_districts.groupby("district").size().reset_index(name="school_count")

# Step 3: Merge the counts with the original district layer
# Adds the 'school_count' column to each district polygon
districts_with_counts = districts_gdf.merge(school_counts, on="district", how="left")

# Step 4: Replace missing values (districts with zero schools) with 0
districts_with_counts["school_count"] = districts_with_counts["school_count"].fillna(0)

## Choropleth Map: Number of Schools per District

This choropleth map visualizes the **distribution of schools across Berlin's administrative districts**. Each district is shaded according to the **total number of schools located within its boundaries**.

### What This Map Shows:
- Darker blue districts have a **higher number of schools**, suggesting better infrastructure density or larger populations.
- Lighter districts have **fewer schools**, which may indicate:
  - Lower population density
  - Fewer residential areas
  - Or possible gaps in educational services

---

### Key Observations:
- Central districts such as **Mitte** and **Charlottenburg-Wilmersdorf** tend to have a **higher concentration of schools**, reflecting their urban character and population density.
- Peripheral districts like **Treptow-Köpenick** or **Spandau** show fewer schools, possibly due to their larger area and lower development intensitypment intens.

---

### Why This Matters in Urban Planning:
- Helps assess **equity in access to educational facilities**
- Can highlight **over-concentration** or **under-provision** of services
- Informs **resource allocation**, zoning policies, and i

In [17]:
# Step 1: Create the base map centered on Berlin
choropleth_map = folium.Map(
    location=[52.52, 13.405],  # Latitude and longitude of centre Berlin
    zoom_start=11,             # Zoom level
    tiles='CartoDB positron'   # Clean, modern basemap
)

# Step 2: Add a choropleth layer to visualize school counts
folium.Choropleth(
    geo_data=districts_with_counts,         # GeoDataFrame containing the geometry and counts
    data=districts_with_counts,             # Data source for color values
    columns=["district", "school_count"],   # Column used for mapping
    key_on="feature.properties.district",   # Match 'district' in GeoJSON to DataFrame
    fill_color="Blues",                     # Color scale (light to dark blue)
    fill_opacity=0.7,                       # Transparency of fill
    line_opacity=0.3,                       # Border transparency
    nan_fill_color="white",                 # Fill color for missing data
    legend_name="Number of Schools per District"  # Legend title
).add_to(choropleth_map)

# Step 3: Add tooltip interactivity for user hover
folium.GeoJson(
    districts_with_counts,                 # GeoData with added school count column
    style_function=lambda feature: {       # District borders (not filled again)
        "fillOpacity": 0,
        "color": "black",
        "weight": 1
    },
    tooltip=folium.GeoJsonTooltip(         # Show info when hovering over a district
        fields=["district", "school_count"],
        aliases=["District:", "Schools:"]
    )
).add_to(choropleth_map)

# Step 4: Add layer control (useful if you add more layers later)
folium.LayerControl().add_to(choropleth_map)

# Step 5: Display the map
choropleth_map

In [27]:
# Step 2: Reproject school points to UTM for accurate buffering
schools_proj = schools_points_cleaned.to_crs(epsg=32633)

# Step 3: Create 500m and 800m buffer zones
schools_proj["buffer_500m"] = schools_proj.geometry.buffer(500)
schools_proj["buffer_1000m"] = schools_proj.geometry.buffer(1000)

# Step 4: Dissolve the buffers into single unified zones
buffer_500m = schools_proj[["buffer_500m"]].rename(columns={"buffer_500m": "geometry"}).set_geometry("geometry").dissolve()
buffer_800m = schools_proj[["buffer_1000m"]].rename(columns={"buffer_1000m": "geometry"}).set_geometry("geometry").dissolve()

# Step 5: Reproject all layers to WGS84 (for folium)
buffer_500m = buffer_500m.to_crs(epsg=4326)
buffer_800m = buffer_800m.to_crs(epsg=4326)
districts_gdf = districts_gdf.to_crs(epsg=4326)

# Step 6: Create folium map centered on Berlin
map_access = folium.Map(location=[52.52, 13.405], zoom_start=11, tiles='CartoDB positron')

# Step 7: Add 800m buffer (light blue)
folium.GeoJson(
    buffer_800m,
    name="1000m Buffer",
    style_function=lambda x: {
        "fillColor": "#a6bddb",
        "color": "#a6bddb",
        "weight": 1,
        "fillOpacity": 0.3
    },
    tooltip="1000m Accessibility Zone"
).add_to(map_access)

# Step 8: Add 500m buffer (darker blue)
folium.GeoJson(
    buffer_500m,
    name="500m Buffer",
    style_function=lambda x: {
        "fillColor": "#045a8d",
        "color": "#045a8d",
        "weight": 1,
        "fillOpacity": 0.4
    },
    tooltip="500m Accessibility Zone"
).add_to(map_access)

# Step 9: Add district boundaries for context
folium.GeoJson(
    districts_gdf,
    name="District Boundaries",
    style_function=lambda x: {
        "color": "black",
        "weight": 1.5,
        "fillOpacity": 0
    },
    tooltip=folium.GeoJsonTooltip(fields=["district"], aliases=["District"])
).add_to(map_access)

for index, row in schools_points_cleaned.to_crs(epsg=4326).iterrows():
    if row.geometry.geom_type == "Point":
        folium.CircleMarker(
            location=[row.geometry.y, row.geometry.x],
            radius=3,
            color="orange",
            fill=True,
            fill_color="orange",
            fill_opacity=0.9,
            popup=row.get("name", "Unnamed School")
        ).add_to(map_access)
        
# Step 10: Add layer control
folium.LayerControl().add_to(map_access)

# Display the map
map_access

## Accessibility Analysis: Buffer Zones Around Schools

In this analysis, we assess school accessibility by creating **buffer zones** representing walkable distances:

- **500 meters** ≈ 6–7 minutes walking distance
- **1000 meters** ≈ extended walk or short bike ride

### Key Observations:
- **Central Berlin** is densely covered by both 500m and 1000m buffers, indicating strong walkable access to schools.
- **Outer districts**, especially in the **north, southeast, and far west**, show visible gaps in 500m coverage.

### But Buffer ≠ Accessibility (On Its Own)

Creating a buffer just gives us a geometric area.

To analyze **accessibility**, we must ask:  
**“Who or what is located within that buffer zone?”**

---

### How to Use Buffers for Accessibility Analysis

1. **Create Buffers**  
   Example: 500m around each school.

2. **Overlay with Other Data**  
   - Districts → What % of each district is covered?
   - Population data → How many people live inside the buffer?
   - Buildings → Which parcels are reachable?



In [20]:
# Reproject to a metric CRS (for accurate distance)
schools_proj = schools_points_cleaned.to_crs(epsg=32633)
districts_proj = districts_gdf.to_crs(epsg=32633)

# Compute centroids of districts
districts_proj["centroid"] = districts_proj.geometry.centroid
district_centroids = districts_proj.set_geometry("centroid")

# Create a unary union of school points for fast lookup
#school_union = schools_proj.unary_union

# Function to find nearest school point to a district centroid
def get_nearest_school_geom(centroid_geom):
    nearest_geom = nearest_points(centroid_geom, school_union)[1]
    return nearest_geom

# Apply function to get nearest school geometry
district_centroids["nearest_school_geom"] = district_centroids["centroid"].apply(get_nearest_school_geom)

# Convert nearest school geometry to GeoSeries for distance calculation
nearest_schools_gs = gpd.GeoSeries(district_centroids["nearest_school_geom"], crs=district_centroids.crs)

# Calculate distance in meters
district_centroids["distance_to_nearest_school_m"] = district_centroids.geometry.distance(nearest_schools_gs)

C:\Users\dmz-admin\AppData\Local\Temp\ipykernel_17328\2481325351.py:10: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  school_union = schools_proj.unary_union


In [21]:
nearest_school_gs = gpd.GeoSeries(district_centroids["nearest_school_geom"], crs=32633)

# Step 2: Reproject the school points to WGS84
nearest_school_wgs84 = nearest_school_gs.to_crs(epsg=4326)

# Step 3: Add to the GeoDataFrame
district_centroids["nearest_school_geom_wgs84"] = nearest_school_wgs84

In [22]:
district_centroids_4326 = district_centroids.to_crs(epsg=4326)

In [23]:
# Create base map
m = folium.Map(location=[52.52, 13.405], zoom_start=11, tiles="CartoDB positron")

# --- Add Administrative (Berlin outer) boundary ---
folium.GeoJson(
    data=districts_gdf,  # full boundary layer
    name="Berlin Boundary",
    style_function=lambda feature: {
        "color": "black",
        "weight": 2,
        "fillOpacity": 0
    },
    tooltip=folium.GeoJsonTooltip(fields=["district"], aliases=["District"])
).add_to(m)

# --- Add district centroids ---
for _, row in district_centroids_4326.iterrows():
    folium.CircleMarker(
        location=[row.centroid.y, row.centroid.x],
        radius=5,
        color="blue",
        fill=True,
        fill_color="blue",
        fill_opacity=0.9,
        popup=f"{row['district']}<br>{round(row['distance_to_nearest_school_m'], 1)} m"
    ).add_to(m)

# --- Add nearest schools ---
for _, row in district_centroids_4326.iterrows():
    school = row["nearest_school_geom_wgs84"]
    folium.CircleMarker(
        location=[school.y, school.x],
        radius=4,
        color="orange",
        fill=True,
        fill_color="orange",
        fill_opacity=1
    ).add_to(m)

    folium.PolyLine(
        locations=[
            [row.centroid.y, row.centroid.x],
            [school.y, school.x]
        ],
        color="red",
        weight=2,
        tooltip=f"{row['district']}: {round(row['distance_to_nearest_school_m'], 1)} m"
    ).add_to(m)

# --- Add Layer Control ---
folium.LayerControl().add_to(m)

# Display the map
m

##  Proximity Analysis: Nearest School to Each District

In this analysis, we calculate the straight-line (Euclidean) distance from the **centroid of each Berlin district** to the **nearest school**.

###  Why Is This Important?

Proximity analysis helps urban planners:
- Identify **underserved areas** that are far from schools
- Prioritize **infrastructure investment** in areas with poor access
- Ensure **spatial equity** in educational service distribution
- Understand how **school placement** affects accessibility city-wide

---

###  How It Was Done:

- District geometries were simplified to **centroids** (central points).
- Each centroid was matched to its **nearest school point** using spatial distance calculations.
- Distances were computed in **meters** using a projected coordinate system (UTM).
- A **Folium interactive map** was created to show:
  - Blue markers: District centers
  - Orange markers: Nearest school
  - Red lines: Straight-line connections
  - Tooltips: Exact distance (in meters) from each district to its nearest school

---

###  Key Observations:

- Most central districts have schools located **very close** (under 500 meters), suggesting strong accessibility.
- Several **outer districts** (e.g., in the north and southeast) show **larger distance lines**, revealing potential service gaps or lower density of educational facilities.
- This analysis provides a quick visual method to evaluate where **new schools might be needed**, especially when combined with population data.

---

###  Next Steps:

This analysis could be extended by:
- Replacing straight-line distance with **road network-based travel distance**
- Calculating proximity **from hospitals**, **residences**, or **planned developments**
- Analyzing proximity to **multiple services** (e.g. nearest hospital *and* school)